In [52]:
import pandas as pd
import numpy as np
import timeit
pd.options.display.max_rows = None
pd.options.display.max_columns = None

In [53]:
#This code is to clean my Personal Weather Station data into a form ready for machine learning

In [54]:
#Read in Historical PWS DataFrame that was created

df_histdates_clean = pd.read_csv('C:/Users/okiem/histdates_df_raw.csv')

In [55]:
#Inspect Data

print(df_histdates_clean.info())
print(df_histdates_clean.head(10))

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10074 entries, 0 to 10073
Data columns (total 39 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   Unnamed: 0          10074 non-null  int64  
 1   Ob_Index            10074 non-null  int64  
 2   Station_ID          10074 non-null  object 
 3   Timezone            10074 non-null  object 
 4   Timestamp_UTC       10074 non-null  object 
 5   Timestamp_Local     10074 non-null  object 
 6   epoch               10074 non-null  int64  
 7   Lat                 10074 non-null  float64
 8   Lon                 10074 non-null  float64
 9   solarRadiationHigh  0 non-null      float64
 10  uvHigh              0 non-null      float64
 11  WindDir_Avg         10074 non-null  int64  
 12  Humidity_High       10074 non-null  float64
 13  Humidity_Low        10074 non-null  float64
 14  Humidity_Avg        10074 non-null  float64
 15  qcStatus            10074 non-null  int64  
 16  Temp

In [56]:
#solarRadiationHigh, uvHigh, and PrecipRate have all NULL values...safe to remove these columns. Also, no need for epoch or first Unamed column
df_histdates_clean.drop(['solarRadiationHigh','uvHigh','PrecipRate', 'epoch','Unnamed: 0'], axis=1, inplace=True)

In [57]:
#Inspect qcStatus
# From API Documentiation:
#     uality control indicator:
# -1: No quality control check performed
#  0: This observation was marked as possibly incorrect by our quality control algorithm
#  1: This observation passed quality control checks

passed = df_histdates_clean['qcStatus'].isin(['1']).sum(axis=0)
pos_fail = df_histdates_clean['qcStatus'].isin(['0']).sum(axis=0)
no_check = df_histdates_clean['qcStatus'].isin(['-1']).sum(axis=0)

df_histdates_clean['qcStatus']
print(f'Passed QC Check: {passed}')
print(f'Possibly Incorrect: {pos_fail}')
print(f'No QC Check: {no_check}')

Passed QC Check: 6198
Possibly Incorrect: 3686
No QC Check: 190


In [58]:
#View data that has possible incorrect data
df_histdates_clean.loc[df_histdates_clean['qcStatus'] == 0]

Ob_Index   Station_ID         Timezone         Timestamp_UTC  \
5             5  KOKEDMON233  America/Chicago  2019-08-01T10:59:59Z   
6             6  KOKEDMON233  America/Chicago  2019-08-01T11:59:58Z   
14           14  KOKEDMON233  America/Chicago  2019-08-01T19:59:58Z   
26           26  KOKEDMON233  America/Chicago  2019-08-02T07:59:59Z   
29           29  KOKEDMON233  America/Chicago  2019-08-02T10:59:58Z   
49           49  KOKEDMON233  America/Chicago  2019-08-03T06:59:59Z   
50           50  KOKEDMON233  America/Chicago  2019-08-03T07:59:58Z   
63           63  KOKEDMON233  America/Chicago  2019-08-03T20:59:58Z   
64           64  KOKEDMON233  America/Chicago  2019-08-03T21:59:58Z   
65           65  KOKEDMON233  America/Chicago  2019-08-03T22:59:59Z   
66           66  KOKEDMON233  America/Chicago  2019-08-03T23:59:59Z   
67           67  KOKEDMON233  America/Chicago  2019-08-04T00:59:59Z   
68           68  KOKEDMON233  America/Chicago  2019-08-04T01:59:58Z   
76           76  KOKEDMON233  America/Chicago  2019-08-04T09:59:58Z   
79           79  KOKEDMON233  America/Chicago  2019-08-04T12:59:59Z   
84           84  KOKEDMON233  America/Chicago  2019-08-04T17:59:58Z   
85           85  KOKEDMON233  America/Chicago  2019-08-04T18:59:59Z   
86           86  KOKEDMON233  America/Chicago  2019-08-04T19:59:59Z   
87           87  KOKEDMON233  America/Chicago  2019-08-04T20:59:58Z   
88           88  KOKEDMON233  America/Chicago  2019-08-04T21:59:58Z   
89           89  KOKEDMON233  America/Chicago  2019-08-04T22:59:58Z   
90           90  KOKEDMON233  America/Chicago  2019-08-04T23:59:59Z   
91           91  KOKEDMON233  America/Chicago  2019-08-05T00:59:59Z   
92           92  KOKEDMON233  America/Chicago  2019-08-05T01:59:58Z   
110         110  KOKEDMON233  America/Chicago  2019-08-05T19:59:59Z   
111         111  KOKEDMON233  America/Chicago  2019-08-05T20:59:59Z   
113         113  KOKEDMON233  America/Chicago  2019-08-05T22:59:58Z   
114         114  KOKEDMON233  America/Chicago  2019-08-05T23:59:59Z   
115         115  KOKEDMON233  America/Chicago  2019-08-06T00:59:59Z   
133         133  KOKEDMON233  America/Chicago  2019-08-06T18:59:59Z   
138         138  KOKEDMON233  America/Chicago  2019-08-06T23:59:58Z   
170         170  KOKEDMON233  America/Chicago  2019-08-08T07:59:58Z   
171         171  KOKEDMON233  America/Chicago  2019-08-08T08:59:59Z   
172         172  KOKEDMON233  America/Chicago  2019-08-08T09:59:58Z   
173         173  KOKEDMON233  America/Chicago  2019-08-08T10:59:59Z   
174         174  KOKEDMON233  America/Chicago  2019-08-08T11:59:58Z   
191         191  KOKEDMON233  America/Chicago  2019-08-09T04:59:58Z   
192         192  KOKEDMON233  America/Chicago  2019-08-09T05:59:59Z   
193         193  KOKEDMON233  America/Chicago  2019-08-09T06:59:59Z   
199         199  KOKEDMON233  America/Chicago  2019-08-09T12:59:57Z   
200         200  KOKEDMON233  America/Chicago  2019-08-09T13:59:59Z   
201         201  KOKEDMON233  America/Chicago  2019-08-09T14:59:57Z   
202         202  KOKEDMON233  America/Chicago  2019-08-09T15:59:58Z   
203         203  KOKEDMON233  America/Chicago  2019-08-09T16:59:59Z   
207         207  KOKEDMON233  America/Chicago  2019-08-09T20:59:59Z   
208         208  KOKEDMON233  America/Chicago  2019-08-09T21:59:59Z   
209         209  KOKEDMON233  America/Chicago  2019-08-09T22:59:59Z   
215         215  KOKEDMON233  America/Chicago  2019-08-10T04:59:58Z   
216         216  KOKEDMON233  America/Chicago  2019-08-10T05:59:59Z   
217         217  KOKEDMON233  America/Chicago  2019-08-10T06:59:59Z   
218         218  KOKEDMON233  America/Chicago  2019-08-10T07:59:59Z   
219         219  KOKEDMON233  America/Chicago  2019-08-10T08:59:59Z   
220         220  KOKEDMON233  America/Chicago  2019-08-10T09:59:58Z   
221         221  KOKEDMON233  America/Chicago  2019-08-10T10:59:58Z   
234         234  KOKEDMON233  America/Chicago  2019-08-10T23:59:59Z   
287         287  KOKEDMON233  A

In [59]:
#View basic statistcal info, 
#...which shows Precip having the posiibltiy of erroneous PrecpTotals
df_histdates_clean.loc[df_histdates_clean['qcStatus'] == 0].describe()

Ob_Index           Lat           Lon  WindDir_Avg  Humidity_High  \
count   3686.000000  3.686000e+03  3.686000e+03  3686.000000    3686.000000   
mean    5451.992404  3.566500e+01 -9.757000e+01   195.060228      69.983180   
std     2277.577002  3.697174e-08  1.432655e-07    54.751360      19.739669   
min        5.000000  3.566500e+01 -9.757000e+01     0.000000      19.000000   
25%     3942.750000  3.566500e+01 -9.757000e+01   175.000000      53.000000   
50%     5380.500000  3.566500e+01 -9.757000e+01   198.000000      71.000000   
75%     6908.750000  3.566500e+01 -9.757000e+01   231.000000      88.000000   
max    10056.000000  3.566500e+01 -9.757000e+01   359.000000      99.000000   

       Humidity_Low  Humidity_Avg  qcStatus    Temp_High     Temp_Low  \
count   3686.000000   3686.000000    3686.0  3686.000000  3686.000000   
mean      65.745252     67.896419       0.0    60.311720    57.562398   
std       21.118158     20.428267       0.0    23.262941    22.170250   
min       17.000000     18.400000       0.0    12.000000    10.000000   
25%       47.000000     50.300000       0.0    40.000000    39.000000   
50%       66.000000     68.600000       0.0    57.000000    55.000000   
75%       85.000000     86.600000       0.0    80.000000    76.000000   
max       99.000000     99.000000       0.0   110.000000   107.000000   

          Temp_Avg  WindSpeed_High  WindSpeed_Low  WindSpeed_Avg  \
count  3686.000000     3686.000000    3686.000000    3686.000000   
mean     58.903961        8.155453       1.127238       3.858844   
std      22.695635        4.705490       1.505605       2.832500   
min      10.900000        0.000000       0.000000       0.000000   
25%      39.600000        5.000000       0.000000       1.800000   
50%      56.000000        7.000000       0.000000       3.400000   
75%      77.600000       11.000000       2.000000       5.400000   
max     108.700000       34.000000       9.000000      17.800000   

       WindGust_High  WindGust_Low  WindGust_Avg   DewPt_High    DewPt_Low  \
count    3686.000000   3686.000000   3686.000000  3686.000000  3686.000000   
mean        8.219208      0.144872      5.805372    47.879816    45.622626   
std         4.715657      0.783243      3.766522    17.608156    17.290715   
min         0.000000      0.000000      0.000000     9.000000     6.000000   
25%         5.000000      0.000000      3.100000    33.000000    31.000000   
50%         8.000000      0.000000      5.200000    47.000000    44.000000   
75%        11.000000      0.000000      8.000000    64.000000    61.000000   
max        34.000000     10.000000     23.500000    81.000000    78.000000   

         DewPt_Avg  WindChill_High  WindChill_Low  WindChill_Avg  \
count  3686.000000     3686.000000    3686.000000    3686.000000   
mean     46.731443       60.249132      55.947233      58.285187   
std      17.432253       23.324083      23.884721      23.358025   
min       7.600000       12.000000       6.100000      10.900000   
25%      32.000000       40.000000      35.100000      38.300000   
50%      45.900000       57.000000      55.000000      56.000000   
75%      62.600000       80.000000      76.000000      77.600000   
max      79.300000      110.000000     107.000000     108.700000   

       HeatIndex_High  HeatIndex_Low  HeatIndex_Avg  Pressure_Max  \
count     3686.000000    3686.000000    3686.000000   3686.000000   
mean        62.136354      58.764948      60.384889     29.924441   
std         26.263948      24.195397      25.158785      0.192585   
min         12.000000      10.000000      10.900000     29.300000   
25%         40.000000      39.000000      39.600000     29.800000   
50%         57.000000      55.000000      56.000000     29.920000   
75%         80.800000      76.000000      78.100000     30.050000   
max        128.600000     123.800000     126.300000     30.530000   

       Pressure_Min  PressureTrend   PrecipTotal  
count   3686.000000    3686.000000   36

In [60]:
#Remove erreoneous PrecipTotal data
df_histdates_clean.drop(df_histdates_clean[df_histdates_clean.PrecipTotal > 5.0].index, inplace=True)

In [61]:
#Format Lat column
df_histdates_clean[['Lat','Lon']] = df_histdates_clean[['Lat','Lon']].round(2)

In [62]:
#Format Datetime into seperate columns and also Index Timestamp
df_histdates_clean[['YEAR','MONTH','DAY', 'TIME_UTC']] = df_histdates_clean['Timestamp_UTC'].str.split('\-|T',expand=True) #Break into seperate columns for flexability 
df_histdates_clean.drop(['Timestamp_UTC'], inplace=True, axis=1) #Remove column after parsing
df_histdates_clean['Timestamp_Local'] =  pd.to_datetime(df_histdates_clean['Timestamp_Local'], infer_datetime_format=True)#Make Local Timestamp the Indexing Column for time series


In [63]:
df_histdates_clean = df_histdates_clean.set_index(df_histdates_clean['Timestamp_Local'])

In [64]:
#Reorder Columns 
df_histdates_clean = df_histdates_clean[['Ob_Index','YEAR', 'MONTH', 'DAY', 'TIME_UTC', 'Timezone', 'Station_ID', 'Lat', 'Lon','Temp_High', 'Temp_Low', 'Temp_Avg', 'WindDir_Avg', 'WindSpeed_High','WindSpeed_Low', 'WindSpeed_Avg', 'WindGust_High', 'WindGust_Low','WindGust_Avg', 'Humidity_High', 'Humidity_Low', 'Humidity_Avg','WindChill_High', 'WindChill_Low', 'WindChill_Avg', 'HeatIndex_High','HeatIndex_Low', 'HeatIndex_Avg', 'Pressure_Max', 'Pressure_Min','PressureTrend', 'PrecipTotal']]

In [65]:
#Export DataFrame at CSV file
df_histdates_clean.to_csv('C:/Users/okiem/histdates_df_clean.csv')